We have dataset containing coordinate information of the location of Cardiac Arrest, and vectors such as AED, MUG, PIT and AMB. Beyond that, we also have information about how long does it take for vectors to response and arrive at the intervention for rescure.
We have plotted the locations on the same map and identified an uneven distribution of Cardiac Arrest and vectors across Belgium. We want to understand how the distribution of cardiac arrest and vectors changes in different region in Belgium. To understand this variation, we want to cluster Cardiac Arrest, and vectors and generate a choropleth map. 

1. Cluster Belgium by Density of Cardiac Arrest, show the choropleth map

2. Cluster Belgium by Density of # AED + # MUG + #PIT + # AMB, , show the choropleth map

3. Cluster Belgium by urgency score, , show the choropleth map
Urgency Score: # Cardiac Arrest / (# AED + # MUG + #PIT + # AMB + 1)

4. distribution of intervention based on distance from vectors and AED

5. Cluster Belgium by intervention time

6. Population / age / wealth density in Belgium?

7. what other information I can obtain from google map?
 tranffic?
 area for resident / work / commercial / entertain / others


### Create choropleth map of vectors in Belgium based on different postal code

In [1]:
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt

In [3]:
# access to OpenStreetMap to gather shapefile data of Belgium
url = 'https://download.geofabrik.de/europe/belgium-latest-free.shp.zip'
gdf = gpd.read_file(url)


In [55]:
# show the first 5 rows of the data
gdf.shape

(2113349, 7)

In [56]:
gdf['area'] = gdf.area
gdf

/var/folders/cv/bbbq9ykj0jg6pt6c7tx5_vjh0000gn/T/ipykernel_13392/1520969213.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'area' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf['area'] = gdf.area


osm_id  code    fclass                                      name  \
0          4414121  1500  building                                      None   
1          5051109  1500  building  Les Tritons - Piscine communale couverte   
2          8103697  1500  building                                 Belle-Île   
3          8109340  1500  building                                      None   
4          8113202  1500  building                                La Boverie   
...            ...   ...       ...                                       ...   
2113344  502870546  1500  building                                      None   
2113345  502870547  1500  building                                      None   
2113346  502870548  1500  building                                      None   
2113347  502873504  1500  building                                      None   
2113348  502873505  1500  building                                      None   

                  type                                           geometry  \
0                 None  POLYGON ((4.45072 51.18915, 4.45072 51.18916, ...   
1        sports_centre  POLYGON ((3.82437 50.71359, 3.82440 50.71370, ...   
2           commercial  POLYGON ((5.59103 50.61679, 5.59132 50.61705, ...   
3                 None  POLYGON ((4.71432 50.88237, 4.71434 50.88237, ...   
4                 None  POLYGON ((5.57711 50.62777, 5.57711 50.62777, ...   
...                ...                                                ...   
2113344           None                                               None   
2113345           None                                               None   
2113346           None                                               None   
2113347           None                                               None   
2113348           None                                               None   

                 area  
0        5.765725e-07  
1        1.539714e-07  
2        4.934537e-06  
3        1.612787e-07  
4        3.881667e-07  
...               ...  
2113344           NaN  
2113345           NaN  
2113346           NaN  
2113347           NaN  
2113348           NaN  

[2113349 rows x 7 columns]

### import external postal geojson file

In [96]:
pc = gpd.read_file("/Users/camillecu/Downloads/KUL/MDA/project/georef-belgium-postal-codes.geojson")

In [ ]:
pc

### import AED geojson

In [57]:
# input a geojson file
aed = gpd.read_file("/Users/camillecu/Downloads/KUL/MDA/project/Visualization/Created GeoJSON Files/AED_GEO.geojson")

In [58]:
aed.shape

(10626, 11)

In [32]:
aed.head()

id              address  number  postal_code municipality province  \
0  13.0  blvd. fr. roosevelt      24         7060     soignies  hainaut   
1  70.0      ch. de wégimont      76         4630      ayeneux    liège   
2  74.0   rue des prémontrès      12         4020        liège    liège   
3  75.0    route de bastogne       1         4920        harzé    liège   
4  76.0          rue du parc       1         4540        jehay    liège   

                                 unique_address       points_coordinates  \
0  blvd. fr. roosevelt,24,7060,soignies,hainaut  (4.0655019, 50.5767646)   
1         ch. de wégimont,76,4630,ayeneux,liège  (5.7397828, 50.6105697)   
2        rue des prémontrès,12,4020,liège,liège  (5.5739754, 50.6380181)   
3          route de bastogne,1,4920,harzé,liège  (5.6658992, 50.4411102)   
4                rue du parc,1,4540,jehay,liège  (5.3231573, 50.5772875)   

         lat       lng              geometry_aed  
0  50.576765  4.065502  POINT (4.06550 50.57676)  
1  50.610570  5.739783  POINT (5.73978 50.61057)  
2  50.638018  5.573975  POINT (5.57398 50.63802)  
3  50.441110  5.665899  POINT (5.66590 50.44111)  
4  50.577287  5.323157  POINT (5.32316 50.57729)

In [59]:
# rename geometry column to geometry_aed
aed.rename(columns={'geometry': 'geometry_aed'}, inplace=True)

In [60]:
# set column geometry_aed as geometry
aed = aed.set_geometry('geometry_aed')

In [61]:
# count unique values in the postal_code column
aed['postal_code'].nunique()

956

In [62]:

# create a new dataframe with the number of AEDs in each postal_code as the second column and the postal_code as the first column
aed_count = aed['postal_code'].value_counts().reset_index()
aed_count.columns = ['postal_code', 'count_postal_code']
aed_count

postal_code  count_postal_code
0           1000                325
1           4000                166
2           9000                158
3           1070                108
4           3600                101
..           ...                ...
951         4601                  1
952         5022                  1
953         5364                  1
954         3293                  1
955         3806                  1

[956 rows x 2 columns]

In [63]:
# merge gdf and aed if geometry_aed column of aed is within geometry column of gdf
bel_aed = gpd.sjoin(gdf, aed, how='left', op='contains')

/Users/camillecu/Downloads/KUL/MDA/project/waffle/lib/python3.11/site-packages/IPython/core/interactiveshell.py:3493: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if await self.run_code(code, result, async_=asy):


In [66]:
bel_aed

(2113421, 11)

In [65]:
# create a subset of aed_in_belgium and drop 'id', 'number', 'index_right',	'osm_id','code' columns
bel_aed = bel_aed.drop(columns=['osm_id','code', 'name', 'index_right','id', 'address','number','fclass'])

In [88]:
# merge bel_aed and aed_count on the postal_code column and left join
bel_aed_count = pd.merge(bel_aed, aed_count, on='postal_code')

In [83]:
# create a new column in bel_aed_count called 'aed_density' which is the number of AEDs in each postal_code divided by the area of the postal_code
bel_aed_count['aed_density'] = bel_aed_count['count_postal_code'] / bel_aed_count['area']

In [84]:
bel_aed_count

fclass           type  \
0        building           None   
1        building  sports_centre   
2        building     commercial   
3        building           None   
4        building           None   
...           ...            ...   
2113416  building           None   
2113417  building           None   
2113418  building           None   
2113419  building           None   
2113420  building           None   

                                                  geometry          area  \
0        POLYGON ((4.45072 51.18915, 4.45072 51.18916, ...  5.765725e-07   
1        POLYGON ((3.82437 50.71359, 3.82440 50.71370, ...  1.539714e-07   
2        POLYGON ((5.59103 50.61679, 5.59132 50.61705, ...  4.934537e-06   
3        POLYGON ((4.71432 50.88237, 4.71434 50.88237, ...  1.612787e-07   
4        POLYGON ((5.57711 50.62777, 5.57711 50.62777, ...  3.881667e-07   
...                                                    ...           ...   
2113416                                               None           NaN   
2113417                                               None           NaN   
2113418                                               None           NaN   
2113419                                               None           NaN   
2113420                                               None           NaN   

         postal_code municipality province  \
0                NaN          NaN      NaN   
1                NaN          NaN      NaN   
2             4020.0        liège    liège   
3                NaN          NaN      NaN   
4                NaN          NaN      NaN   
...              ...          ...      ...   
2113416          NaN          NaN      NaN   
2113417          NaN          NaN      NaN   
2113418          NaN          NaN      NaN   
2113419          NaN          NaN      NaN   
2113420          NaN          NaN      NaN   

                             unique_address              points_coordinates  \
0                                       NaN                             NaN   
1                                       NaN                             NaN   
2        quai des vennes,1,4020,liège,liège  (5.5937472, 50.61574659999999)   
3                                       NaN                             NaN   
4                                       NaN                             NaN   
...                                     ...                             ...   
2113416                                 NaN                             NaN   
2113417                                 NaN                             NaN   
2113418                                 NaN                             NaN   
2113419                                 NaN                             NaN   
2113420                                 NaN                             NaN   

               lat       lng  count_postal_code   aed_density  
0              NaN       NaN                NaN           NaN  
1              NaN       NaN                NaN           NaN  
2        50.615747  5.593747               60.0  1.215919e+07  
3              NaN       NaN                NaN           NaN  
4              NaN       NaN                NaN           NaN  
...            ...       ...                ...           ...  
2113416        NaN       NaN                NaN           NaN  
2113417        NaN       NaN                NaN           NaN  
2113418        NaN       NaN                NaN           NaN  
2113419        NaN       NaN                NaN           NaN  
2113420        NaN       NaN                NaN           NaN  

[2113421 rows x 13 columns]

In [71]:
bel_aed_count.columns

Index(['fclass', 'type', 'geometry', 'area', 'postal_code', 'municipality',
       'province', 'unique_address', 'points_coordinates', 'lat', 'lng',
       'count_postal_code', 'aed_density'],
      dtype='object')

In [93]:
# use folium to create Choropleth map of 'aed_density', 'count_postal_code' in Belgium
import folium

m = folium.Map(location=[50.8503, 4.3517], zoom_start=10)

folium.Choropleth(
    geo_data=bel_aed_count,
    name='choropleth',
    data=bel_aed_count,
    columns=['postal_code','count_postal_code'],
    key_on='feature.properties.postal_code',
    fill_color='BuPu',
    fill_opacity=0.7,
    line_opacity=1.0,
    legend_name='AED Density in Belgium'
).add_to(m)

folium.LayerControl().add_to(m)

#m.save('AED_Density_Belgium.html')
display(m)



### clustering method
- K-means
- hierarchial
- DBSCAN
- Gaussian 